# Imports

In [1]:
import numpy as np
import meshplot as mp
from PatchGeneration.Modules.Mesh import *
from PatchGeneration.Modules.PatchCollector import *
from DenoisingGCN.GCNModel import *
from DenoisingGCN.datautils import *
import igl

# Push Matlab files through GCN
Now since we have example matlab files for the example armadillo mesh, we want to train a GCN model for the example files and see how it performs. Training the a model is currently done in command line. A model has been trained.

After training a model, this model can be used to predict normals for a noisy mesh. In then codeblock below, we first generate a noisy model.

In [5]:
NAME = "fandisk"
NOISE_LEVEL = 2
TEST_MESH_FILE = f"./models/{NAME}.obj"
test_mesh = Mesh.readFile(TEST_MESH_FILE)
_ = test_mesh.applyGaussianNoise(NOISE_LEVEL / 10)

Random average displacement: 0.0037081266274905


Visualizing the newly created noisy model:

In [6]:
v = np.concatenate((test_mesh.v, test_mesh.noisy_v), axis=0)
v[test_mesh.v.shape[0]:, 0] += test_mesh.getPCBoundingBox()[0] * 1.1
f = np.tile(test_mesh.f, (2, 1))
f[test_mesh.f.shape[0]:] += test_mesh.v.shape[0]
color = np.ones(2*test_mesh.f.shape[0])
color[:test_mesh.f.shape[0]] = 0
mp.plot(v, f, c=color)

Renderer(camera=PerspectiveCamera(children=(DirectionalLight(color='white', intensity=0.6, position=(53.008010…

For this model, we need to create patches and save the patches to use them later to pass through the GCN. In the following codeblock, we generate and save the patches!

In [7]:
SAVE_PATH = "./samples/test_" + NAME

noise_levels = np.arange(1, 4, 1)
print(f"Creating patches for noise levels: {noise_levels}")
for noise_level in noise_levels:
    factor = noise_level/10
    test_mesh.applyGaussianNoise(factor)
    
    collector = PatchCollector(test_mesh)
    collector.collectAndSavePatches(SAVE_PATH)

Creating patches for noise levels: [1 2 3]
Random average displacement: 0.0003754239381888797
Start selecting patches
Patch 1/12946 selected!
Patch 2/12946 selected!
Patch 3/12946 selected!
Patch 4/12946 selected!
Patch 5/12946 selected!
Patch 6/12946 selected!
Patch 7/12946 selected!
Patch 8/12946 selected!
Patch 9/12946 selected!
Patch 10/12946 selected!
Patch 11/12946 selected!
Patch 12/12946 selected!
Patch 13/12946 selected!
Patch 14/12946 selected!
Patch 15/12946 selected!
Patch 16/12946 selected!
Patch 17/12946 selected!
Patch 18/12946 selected!
Patch 19/12946 selected!
Patch 20/12946 selected!
Patch 21/12946 selected!
Patch 22/12946 selected!
Patch 23/12946 selected!
Patch 24/12946 selected!
Patch 25/12946 selected!
Patch 26/12946 selected!
Patch 27/12946 selected!
Patch 28/12946 selected!
Patch 29/12946 selected!
Patch 30/12946 selected!
Patch 31/12946 selected!
Patch 32/12946 selected!
Patch 33/12946 selected!
Patch 34/12946 selected!
Patch 35/12946 selected!
Patch 36/12946 s

### Loading the trained GCN model

In [ ]:
EPOCH_MODEL = 8
MODEL_PATH = f"./DenoisingGCN/checkpoints/{EPOCH_MODEL}_model.t7"

dgcnn = DGCNN(8, 17, 1024, 0.5)
dgcnn.load_state_dict(torch.load(MODEL_PATH))
dgcnn.cuda()
dgcnn.eval()
print("Loading DGCNN in GPU complete!")

Loading DGCNN in GPU complete!


In [ ]:
BATCH_SIZE = 8

class FAKE_K_OPT_CLASS():
    
    def __init__(self):
        self.batch_size = BATCH_SIZE
        self.num_workers = 8
        self.num_neighbors = 64

FAKE_K_OPT = FAKE_K_OPT_CLASS()

data_path = {"data_path": [SAVE_PATH + "/" + x for x in os.listdir(SAVE_PATH) if x.startswith(str(NOISE_LEVEL))]}
data_path = np.array(data_path["data_path"])

k_opt = FAKE_K_OPT
test_dataset = MatrixDataset(k_opt, data_path, k_opt.num_neighbors, is_train=False)
test_data_loader = test_dataset.getDataloader()

outputs = None

print(f"Number of data: {len(data_path)}\nNumber of batches: {int(len(data_path)/BATCH_SIZE)}")
for i_test, data in enumerate(test_data_loader, 0):
    inputs, _, gt_norm, _ = data
    inputs = inputs.type(torch.FloatTensor)
    inputs = inputs.permute(0, 2, 1)

    inputs = inputs.cuda()

    output = dgcnn(inputs)
    numpy_output = output.cpu().detach().numpy()

    if i_test == 0:
        outputs = numpy_output
    else:
        outputs = np.concatenate((outputs, numpy_output), axis=0)

# Pass residual patches through the network one by one
res = len(data_path) % BATCH_SIZE
res_indices = np.arange(len(data_path))[-res:]
for index in res_indices:
    inputs, _, gt_norm, _ = test_dataset[index]
    inputs = torch.from_numpy(inputs.reshape(1, inputs.shape[0], -1))
    gt_norm = torch.from_numpy(gt_norm)
    
    inputs = inputs.type(torch.FloatTensor)
    inputs = inputs.permute(0, 2, 1)

    inputs = inputs.cuda()

    output = dgcnn(inputs)
    numpy_output = output.cpu().detach().numpy()
    
    outputs = np.concatenate((outputs, numpy_output), axis=0)

print(f"Number of outputs: {len(outputs)}")

Number of data: 12946
Number of batches: 1618
Number of outputs: 12946


### Visualize predicted normals
Before visualizing the normals, the output of the GCN needs to be transformed back to the original coordinate system of the face. First we read all the rotation matrices that were used to transform the patches and then use those to reorient the output normals to the normals that were predicted.

In [ ]:
files = os.listdir(SAVE_PATH)
N = test_mesh.f.shape[0]
rotation_matrices = np.zeros((N, 3, 3))

for file_name in files:
    file_path = SAVE_PATH + "/" + file_name
    noise_level_str, index_str = file_name.split(".")[0].split("_")
    index = int(index_str)
    if int(noise_level_str) != NOISE_LEVEL:
        # We don't need to print every file that we skip..
        continue
    elif index >= N:
        print(f"File {file_name} contains an index that is too large for this mesh.")
        continue
    rotation_matrices[index, :, :] = np.array(sio.loadmat(file_path)["ROT"])

rotation_matrices = rotation_matrices[:outputs.shape[0]]

<function print>

In [ ]:
plot = mp.plot(test_mesh.noisy_v, test_mesh.f)
center = igl.barycenter(test_mesh.noisy_v, test_mesh.f)[:outputs.shape[0]]
print(outputs.shape, rotation_matrices.shape)
predictions = np.einsum('ij,ijk->ik', outputs, rotation_matrices)
plot.add_lines(center, center + predictions, shading={"line_color": "blue"})
plot.add_lines(center, center + test_mesh.getFaceNormals(True)[:outputs.shape[0]], shading={"line_color": "red"})
plot.add_lines(center, center + test_mesh.getFaceNormals(False)[:outputs.shape[0]], shading={"line_color": "green"})

Renderer(camera=PerspectiveCamera(children=(DirectionalLight(color='white', intensity=0.6, position=(24.897219…

(12946, 3) (12946, 3, 3)


3

In [ ]:
print(f"Average dot product with output and face normal vectors: {np.median(np.sum(test_mesh.getFaceNormals(False)[:outputs.shape[0]] * predictions, axis=1) / np.linalg.norm(outputs, axis=1))}")
print(f"Average dot product with output and x-axis: {np.median(np.sum(test_mesh.getFaceNormals(False)[:outputs.shape[0]] * test_mesh.getFaceNormals(True)[:outputs.shape[0]], axis=1))}")


Average dot product with output and face normal vectors: 0.9991078412989591
Average dot product with output and x-axis: 0.9981420784721164


In [ ]:
N = 100000
random_sample = np.random.normal(size=(N, 3))
random_direction = random_sample / np.linalg.norm(random_sample, axis=1)[:, None]

# stdev = 100/100
# random_gaussian_sample = np.random.normal(0, stdev, (N, 1))
# noise = random_direction * np.tile(random_gaussian_sample, (1, 3))
axes = np.identity(3)
c = (1./3.)**(1./2.)
corners = np.array([[c, c, c], [-c, c, c], [-c, -c, c]])
print(np.sum(np.einsum("ni,ij->nj", random_direction, axes)>0.8)/N)
print(np.sum(np.einsum("ni,ij->nj", random_direction, corners)>0.8)/N)


0.30009
0.29943
